In [2]:
# configure image-magick
from moviepy.config import change_settings
change_settings({"IMAGEMAGICK_BINARY": r"C:\Program Files\ImageMagick-7.1.1-Q16-HDRI\magick.exe"})

import moviepy.editor as mpy
from PIL import Image
import IPython.display as ipd
from glob import glob
import os
import subprocess
from textwrap import wrap
from pathlib import Path

In [3]:
# Helper function to parse an srt
def parse_srt(srt_path):
    """
    Parse an SRT file and return a list of subtitle entries.
    Each entry is a dictionary with 'start', 'end', and 'text' keys.
    """
    subtitles = []
    with open(srt_path, "r", encoding="utf-8") as file:
        content = file.read().strip().split("\n\n")
        for block in content:
            lines = block.split("\n")
            if len(lines) >= 3:
                time_range = lines[1]
                start, end = time_range.split(" --> ")
                text = " ".join(lines[2:])
                subtitles.append({
                    "start": parse_time(start),
                    "end": parse_time(end),
                    "text": text
                })
    return subtitles


def parse_time(timestamp):
    """
    Parse an SRT timestamp (e.g., '00:00:05,000') into seconds.
    """
    h, m, s = timestamp.replace(",", ".").split(":")
    return float(h) * 3600 + float(m) * 60 + float(s)


def create_subtitle_clip(subtitle, video_width):
    """
    Create a subtitle text clip for a given subtitle entry.
    """
    wrapped_text = "\n".join(wrap(subtitle["text"], width=40))  # Adjust width as needed
    font_size = 40
    text_clip = (
        mpy.TextClip(wrapped_text, fontsize=font_size, color="Red", bg_color="White")
        .set_position(("center", "bottom"))
        .set_start(subtitle["start"])
        .set_duration(subtitle["end"] - subtitle["start"])
    )
    return text_clip


def create_text_clip(line, start, duration, video_width, video_height):
    """
    Create a text clip that dynamically adjusts to fit within the video dimensions.
    
    Parameters:
    - line: The text to display.
    - start: Start time for the text.
    - duration: Duration for which the text is displayed.
    - video_width: The width of the video.
    - video_height: The height of the video.
    """
    max_width = video_width * 0.9  # 90% of video width
    max_height = video_height * 0.2  # Use 20% of video height for text
    font_size = 40  # Start with an initial font size

    while True:
        # Dynamically wrap the text to fit within max_width
        wrapped_text = "\n".join(wrap(line, width=int(max_width / (font_size / 2))))
        text_clip = mpy.TextClip(wrapped_text, fontsize=font_size, color="black", bg_color="white")

        # Check if the text fits within the allowed dimensions
        if text_clip.w <= max_width and text_clip.h <= max_height:
            break

        # Reduce font size if it doesn't fit
        font_size -= 2
        if font_size < 10:  # Prevent infinite loop for very long text
            raise ValueError("Text cannot fit within the defined window. Consider shortening the text.")

    # Center the text clip and set its start time and duration
    return text_clip.set_position("center").set_start(start).set_duration(duration)

   
# File paths
audio_path = Path(r"why_python.mp3")
srt_path = Path(r"Why_python.srt")
text_file_path = Path(r"why_python.txt")
image_paths = [
    r"WhyPythonPics/Python programming language.png",
    r"WhyPythonPics/data analysis.png",
    r"WhyPythonPics/data analysis (1).png",
    r"WhyPythonPics/African people in web development.png",
    r"WhyPythonPics/African people in mobile app development.png"
]

# Validate audio file
if not audio_path.exists():
    raise FileNotFoundError(f"Audio file not found: {audio_path}")

# Validate subtitle file
if not srt_path.exists():
    raise FileNotFoundError(f"SRT file not found: {srt_path}")

# Validate text file
if not text_file_path.exists():
    raise FileNotFoundError(f"Text file not found: {text_file_path}")

# Validate images
for path in image_paths:
    if not os.path.exists(path):
        raise FileNotFoundError(f"Image file not found: {path}")

# Load audio
audio = mpy.AudioFileClip(str(audio_path))
audio_duration = audio.duration  # Match video duration to audio duration

# Video specifications
video_width, video_height, fps = 1280, 720, 24

# Create slideshow background
num_images = len(image_paths)
duration_per_image = audio_duration / num_images
slideshow_clips = [
    mpy.ImageClip(path)
    .resize(width=video_width, height=video_height)  # Resize while maintaining aspect ratio
    .set_duration(duration_per_image)  # Set duration for each image
    for path in image_paths
]
background = mpy.concatenate_videoclips(slideshow_clips, method="compose").set_fps(fps)

# Parse subtitles and create subtitle clips
subtitles = parse_srt(srt_path)
subtitle_clips = [
    create_subtitle_clip(sub, video_width) for sub in subtitles
]

# Load transcription text and create text clips
with open(text_file_path, "r", encoding="utf-8") as file:
    lines = [line.strip() for line in file if line.strip()]

# Define start times and durations
start_times = [0, 2, 4, 6, 9, 12, 14, 16, 18, 20, 21, 23, 26, 28, 30, 32,\
              33, 34, 36, 38, 40, 42, 45, 47, 49, 52, 55, 57, 59, 61, 63,\
              65, 67, 70, 72, 74, 76, 79, 81, 82, 86, 88, 90, 93, 96, 98, 100,\
              102, 104, 106, 108, 109, 111, 113, 116, 118, 121, 124, 127, 128,\
              130, 132, 134, 136, 139, 141, 143, 145, 147, 149, 152, 155, 158,\
              159, 161, 163, 166, 169, 171, 173, 175, 176, 179, 180, 182, 184,\
              186, 188, 190, 192, 194, 197, 200, 202, 204, 206, 208, 211] 
durations = [2, 2, 2, 3, 3, 2, 2, 2, 2, 1, 2, 3, 2, 2, 2, 1, 1, 2, 2, 2, 2, 3,\
            2, 2, 3, 3, 2, 2, 2, 2, 2, 2, 3, 2, 2, 2, 3, 2, 1, 4, 2, 2, 3, 3, 2,\
            2, 2, 2, 2, 2, 1, 2, 2, 3, 2, 3, 3, 3, 1, 2, 2, 2, 2, 3, 2, 2, 2, 2,\
            2, 3, 3, 3, 1, 2, 2, 3, 3, 2, 2, 2, 1, 2, 1, 2, 2, 2, 2, 2, 2, 2, 3,\
            3, 2, 2, 2, 2, 3] 
if len(lines) != len(durations):
    raise ValueError("Mismatch: Ensure the number of lines matches start_times and durations.")

text_clips = [
    create_text_clip(line, start, duration, video_width, video_height)
    for line, start, duration in zip(lines, start_times, durations)
]

# Combine all clips
all_clips = [background, *subtitle_clips, *text_clips]
final_video = mpy.CompositeVideoClip(all_clips).set_audio(audio)

# Export the final video
output_path = "final_why_python_video.mp4"
final_video.write_videofile(output_path, fps=fps, codec="libx264", audio_codec="aac", preset="slow")

print(f"Video saved to {output_path}")
ipd.Video("final_why_python_video.mp4", width=650, height=350, embed=True)


Moviepy - Building video final_why_python_video.mp4.
MoviePy - Writing audio in final_why_python_videoTEMP_MPY_wvf_snd.mp4


MoviePy - Done.
Moviepy - Writing video final_why_python_video.mp4



Moviepy - Done !
Moviepy - video ready final_why_python_video.mp4
Video saved to final_why_python_video.mp4


In [4]:
# # Audio file path
# audio_path = Path(r"why_python.mp3")

# # Check if audio file exists
# if not audio_path.exists():
#     raise FileNotFoundError(f"Audio file not found: {audio_path}")

# # Load audio file
# audio = mpy.AudioFileClip(str(audio_path))
# audio_duration = audio.duration  # Get audio duration in seconds
# video_duration = audio_duration  # Set video duration to match audio duration

# # Video specifications
# video_width, video_height, fps = 1280, 720, 24

# # PREPARE BACKGROUND
# # Image paths
# image_paths = [
#     r"WhyPythonPics/Python programming language.png",
#     r"WhyPythonPics/data analysis.png",
#     r"WhyPythonPics/data analysis (1).png",
#     r"WhyPythonPics/African people in web development.png",
#     r"WhyPythonPics/African people in mobile app development.png"
# ]

# # Check if all images exist
# for path in image_paths:
#     if not os.path.exists(path):
#         raise FileNotFoundError(f"Image file not found: {path}")

# # Calculate duration per image
# num_images = len(image_paths)
# duration_per_image = video_duration / num_images

# # Create slideshow clips
# slideshow_clips = [
#     mpy.ImageClip(path)
#     .resize(height=video_height)  # Resize while maintaining aspect ratio
#     .set_duration(duration_per_image)  # Set duration for each image
#     for path in image_paths
# ]

# # Concatenate clips to form the slideshow
# background = mpy.concatenate_videoclips(slideshow_clips, method="compose").set_fps(fps)

# print("Background created successfully.")

# # PREPARE TEXT CLIPS
# # Define start times and durations for each line in seconds
# start_times = [0, 3, 6, 8, 10, 12, 16, 17, 20, 22, 24, 26, 29, 33, 35,\
#                38, 41, 44, 47, 49, 52, 54, 56, 58, 62, 66, 68, 70, 73,\
#               74, 76, 79, 81, 83, 86, 89, 91, 94, 95, 97, 99, 101, 103,\
#               105, 106, 109, 112, 114, 117, 122, 124, 126, 129, 132, 134,\
#               136, 140, 143, 146, 149, 150, 153, 154, 157, 159, 162, 163,\
#               167, 170, 172, 175, 178, 180, 183, 186, 189, 192, 196] 
# durations = [3, 3, 2, 2, 2, 4, 1, 3, 2, 2, 2, 3, 4, 2, 3, 3, 3, 3, 2, 3, 2,\
#             2, 2, 4, 4, 2, 2, 3, 1, 2, 3, 2, 2, 3, 3, 2, 3, 1, 2, 2, 2, 2, 2,\
#             1, 3, 3, 2, 3, 5, 2, 2, 3, 3, 2, 2, 4, 3, 3, 3, 1, 3, 1, 3, 2, 3, 1,\
#             4, 3, 2, 3, 3, 2, 3, 3, 3, 3, 2] 

# # Load transcriptions from a text file
# with open("why_python.txt", "r") as file:
#     lines = [line.strip() for line in file.readlines()]
#     # print(lines)

# # Create and position each text segment
# clips = []
# for line, start, duration in zip(lines, start_times, durations):
#     text_clip = (
#         mpy.TextClip(line, fontsize=50, color='black', bg_color="white")
#         .set_position("center")
#         .set_start(start)
#         .set_duration(duration)
#     )
#     clips.append(text_clip)
#     print("Text clips ready...")
# print(clips)


# # Helper function for dynamic font sizing
# def create_text_clip(line, start, duration, video_width):
#     max_width = video_width * 0.9  # 90% of video width
#     font_size = 50
#     while True:
#         text_clip = mpy.TextClip(line, fontsize=font_size, color='black', bg_color="white")
#         if text_clip.w <= max_width:
#             break
#         font_size -= 2  # Reduce font size until it fits
#     return text_clip.set_position("center").set_start(start).set_duration(duration)

# # Create text clips with dynamic font size
# clips = [
#     create_text_clip(line, start, duration, video_width)
#     for line, start, duration in zip(lines, start_times, durations)
# ]
